### Configuration

Choose which scenario's to include in the comparison

In [1]:
scenarios = {
    'S1': {
        'load':         True,
        'reinitialize': False
    },
    'S2': {
        'load':         True,
        'reinitialize': False
    },
    'S3':{
        'load':         True,
        'reinitialize': False
    },
    'S4':{
        'load':         True,
        'reinitialize': False
    }
}

Choose which keys you want to save in the dataframe

In [2]:
regex = [
    
    # Energies
    'Eprim',
    'Eren',
    'Esto',
    
    'productionSite.Eboi',
    'productionSite.EhpEl',
    'productionSite.Esun',
    'productionSite.Ehp',
    'productionSite.ECHP',
    'productionSite.EelCHP',
    'productionSite.Esto',
    
    'grid.Egrid',
    'grid.Edis',
    'grid.Ehea',
    'grid.Esh',
    'grid.Edhw',
    'grid.EboosEl',
    'grid.Esto',
    
    # Powers
    'Pprim', 
    'Pren',
    'Qsto',
    
    'productionSite.Pboi',
    'productionSite.PhpEl',
    'productionSite.Qsun',
    'productionSite.Qhp',
    'productionSite.PCHP',
    'productionSite.PelCHP',
    'productionSite.Qsto',
    'productionSite.Qren',
    'productionSite.cHP.Qheating',
    
    'grid.Qgrid',
    'grid.Qdis',
    'grid.Qhea',
    'grid.Qsh',
    'grid.Qdhw',
    'grid.Qhp',
    'grid.PboosEl',
    'grid.Qsto',
    
    # Heatingsystems
    '.*TZones',
    '.*TZonem',
    '.*TZoned',
    
    '.*TDhws',
    '.*TDhwm',
    '.*TDhwd.*(?<!\))$',
    
    '.*TSupplym',
    '.*TSupplys',
    
    '.*TGridi',
    '.*TGrido',

    '.*mRad',
    '.*mDhw',
    '.*mDhwReq',
    '.*mSupply',
    
    '.*tan.vol.*T',
    
    # Grid
    '.*Pipe.*QLosses',
    '.*Pipe.*T.Out',
    
    
    # Production site
    '.*COP$',
    '.*modulation$',
    '.*mGrid$',
    'productionSite.Tret.*T',
    
    ## Solar collector parameters
    'productionSite.solar.m_flow',
    'productionSite.TSun.*T',
    #'productionSite.bufferSolar',
    'productionSite.bufferSolar.m_flow',
    'productionSite.bufferSolar.port_a.h_outflow',
    'productionSite.bufferSolar.port_b.h_outflow',
    
    ## Boiler parameters
    #'productionSite.boiler',
    'productionSite.boiler.heatSource.QFinal',
    'productionSite.TBoi.*T',
    
    ## CHP parameters
    #'productionSite.cHP',
    'productionSite.cHP.Qheating',
    #'productionSite.bufferChp',
    'productionSite.bufferChp.m_flow',
    'productionSite.bufferChp.port_a.h_outflow',
    'productionSite.bufferChp.port_b.h_outflow',
    
    ## HP parameters
    #'productionSite.hp',
    'productionSite.*THp.*T',
    #'productionSite.bufferHp',
    'productionSite.bufferHp.m_flow',
    'productionSite.bufferHp.port_a.h_outflow',
    'productionSite.bufferHp.port_b.h_outflow'
    
]

cumul = [
    'Eprim',
    'Eren',
    'Esto',
    'productionSite.Eboi',
    'productionSite.EhpEl',
    'productionSite.Esun',
    'productionSite.Ehp',
    'productionSite.EChpGas',
    'productionSite.EchpEl',
    'productionSite.Esto',
    'grid.Egrid',
    'grid.Edis',
    'grid.Ehea',
    'grid.Esh',
    'grid.Edhw',
    'grid.EboosEl',
    'grid.Esto'
]

Set the result file location

In [3]:
path = r'M:/De schipjes/Scenarios/'
name = r'year 24-08'

### Imports

In [4]:
import os
import sys
import math
import re

import pandas as pd
import numpy as np

from datetime import date
from result import Result, Results, load
from IPython.display import HTML

In [5]:
import charts
charts.default_settings.update(dict(show='tab', stock=True))

Server running in the folder c:\Users\u0098668\Documents\Modelica\DeSchipjes\Notebooks\Analysis at 127.0.0.1:62229


### Initialization

In [6]:
path = os.path.join(path, name)

In [7]:
periods = {
    '1': [[604800, 31556926]],
    '2': [[604800, 15778463], [15778463, 31556926]],
    '3': [[604800, 10518976], [10518976, 21037951], [21037951, 31556926]]
}

In [8]:
def find_keys(regex, result):
    keys = []
    if type(regex) is not list:
        regex = [regex]
    
    for r in regex:
        for k in result.keys:
            if re.match(r, k):
                keys.append(k)
    return list(set(keys))

def load_result(scenario):
    # Find the files with their full path and load the results
    files = filter(lambda x: x.endswith('.mat'), 
        [os.path.join(path, scenario, f) for f in sorted(os.listdir(os.path.join(path, scenario)))])
    return [Result(f) for f in files]

def concat(results, regex):   
    # Get the number of files and calculate the start and stop times 
    n = len(results)
    period = math.ceil(31556926./3)
    
    durations = periods[str(n)]
    
    # Load the dataframes
    dfs = [r.get(regex) for r in results]
    
    # Slice the correct times
    dfs = [dfs[i].truncate(
        before=date.fromtimestamp(durations[i][0]), 
        after=date.fromtimestamp(durations[i][1])) for i in range(0, n)]
    
    # Cumulate the results if necessary
    for i in range(1, n):
        for k in dfs[0].columns:
            if k in cumul:
                dfs[i][k] = dfs[i][k] + dfs[i-1][k][-1]
                
    # Concat the dataframes and save it
    return pd.concat(dfs) 

def load_df(scenario):
    return load(os.path.join(path, scenario, scenario + '.hdf'))

def save_df(df, scenario):
    dest = os.path.join(path, scenario, scenario + '.hdf')
    df.to_hdf(dest, 'data')

In [9]:
data = dict()
results = dict()
for scenario, config in scenarios.iteritems():
    if config['load']:
        if config['reinitialize']:
            results[scenario] = load_result(scenario)
            data[scenario] = concat(results[scenario], regex)
            save_df(data[scenario], scenario)
        else:
            data[scenario] = load_df(scenario)

Some further data manipulations...

In [10]:
loaded_scenarios = []

for k, v in scenarios.iteritems():
    if v['load']:
        loaded_scenarios.append(k)
loaded_scenarios = sorted(loaded_scenarios)

if 'S1' in data:
    data['S1']['Eprim'] = data['S1']['Eprim'] + data['S1']['productionSite.ECHP']
    data['S1']['productionSite.QCHP'] = data['S1']['productionSite.cHP.Qheating']

placeholder = [
    'productionSite.PElChp',
    'productionSite.QCHP',
    'productionSite.PCHP'
]

for s in loaded_scenarios:
    try:
        data[s]['Qboi'] = data[s]['productionSite.boiler.heatSource.QFinal']
        for p in placeholder:
            if p not in data[s]:
                data[s][p] = 0
    except KeyError:
        print 'Qboi failed for scenario {0}'.format(s)


loads = {
    'productionSite.bufferSolar': 'QbufferSolar',
    'productionSite.bufferHp': 'QbufferHp',
    'productionSite.bufferChp': 'QbufferChp'
}     

for s in loaded_scenarios:
    for k, v in loads.iteritems():
        if len(data[s].filter(regex=k).columns) > 0:
            data[s][v] = data[s][k+'.m_flow']*(data[s][k+'.port_a.h_outflow']-data[s][k+'.port_b.h_outflow'])
        else:
            print 'No {0} in scenario {1}'.format(k, s)

No productionSite.bufferHp in scenario S1
No productionSite.bufferSolar in scenario S2
No productionSite.bufferChp in scenario S2
No productionSite.bufferChp in scenario S3
No productionSite.bufferChp in scenario S4


In [11]:
months = []
for i in range(1,12):
    months.append([date(1970, i, 1), date(1970, i+1, 1)])

In [12]:
def monthly_diff(df, key, year=True):
    res = []
    
    dates = months[:]
    
    if year:
        dates.append([date(1970, 1, 1), date(1970, 12, 1)])
    
    for m in dates:
        [i1, i2] = [df.index.searchsorted(m[0]), df.index.searchsorted(m[1])]
        [ix1, ix2] = [df.ix[df.index[i1]], df.ix[df.index[i2]]]
    
        res.append(ix2[key].mean()-ix1[key].mean())
        
    return res

def monthly_average(df, key):
    res = []
    
    for m in months:
        tdf = df.truncate(before=m[0], after=m[1])
        res.append(tdf[key].mean())
        
    return res

def value_or_zero(data, s, y, i):
    try:
        return data[s][y][i]
    except KeyError:
        return 0

### Plots

### Total  Energy consumption / production

In [13]:
categories = [
    'Eprim',
    'Eren',
    'productionSite.Eboi',
    'productionSite.EhpEl',
    'productionSite.Esun',
    'productionSite.Ehp',
    'productionSite.ECHP',
    'productionSite.EelCHP',
    'productionSite.Esto'
]

names = {
    'Eprim': 'Primary Energy',
    'Eren': 'Renewable Energy',
    'productionSite.Eboi': 'Boiler fuel consumption',
    'productionSite.EhpEl': 'Heat pump electricity consumption',
    'productionSite.Esun': 'Solar collector heat production',
    'productionSite.Ehp': 'HP heat production',
    'productionSite.ECHP': 'CHP fuel consumption',
    'productionSite.EelCHP': 'CHP electricity production',
    'productionSite.Esto': 'Storage tank heat losses'
}

options = {
    'chart': {'zoomType': 'xy'},
    'title': {'text': 'Total energy consumption and production'},
    'subtitle': {'text': 'Production site'},
    'xAxis': {
        'categories': map(lambda c: names[c], categories)
    },
    'yAxis': {
        'min': 0,
        'title': {'text': 'Energy in Joule'}
    }
}

series = map(lambda s: {
    'name': s,
    'data': map(lambda y: value_or_zero(data, s, y, -1), categories)
}, loaded_scenarios)

charts.plot(
    type='column', 
    series=series, 
    options=options,
    stock=False,
    show='inline', 
    save=os.path.join(path, options['title']['text']) + '.html')

###Total heat usage

In [23]:
categories = [
    'grid.Egrid',
    'grid.Edis',
    'grid.Ehea',
    'grid.Esh',
    'grid.Edhw',
    'grid.Esto',
    'grid.EboosEl'
]

names = {
    'grid.Egrid': 'Total grid heat demand',
    'grid.Edis': 'Distribution losses',
    'grid.Ehea': 'Heating heat demand',
    'grid.Esh': 'Space heating heat demand',
    'grid.Edhw': 'DHW heat demand',
    'grid.Esto': 'Storage tank losses',
    'grid.EboosEl': 'Booster electricity consumption'
}

options = {
    'chart': {'zoomType': 'xy'},
    'title': {'text': 'Heat usage in the grid'},
    'xAxis': {
        'categories': map(lambda c: names[c], categories)
    },
    'yAxis': {
        'min': 0,
        'title': {'text': 'Energy in Joule'}
    }
}

series = map(lambda s: {
    'name': s,
    'data': map(lambda y: value_or_zero(data, s, y, -1), categories)
}, loaded_scenarios)

charts.plot(
    type='column', 
    series=series, 
    options=options,
    stock=False,
    show='inline', 
    save=os.path.join(path, options['title']['text']) + '.html')

#### Origin of heat production

In [41]:
categories = [
    ['Eprim', 'Eren'],
    ['productionSite.Esun', 'productionSite.Ehp', 'productionSite.ECHP', 'productionSite.Eboi']
]

html = []

for s in loaded_scenarios:
    series = []
    
    for i, cat in enumerate(categories):
        total = sum(map(lambda c: value_or_zero(data, s, c, -1), cat))
        
        series.append({
            'center': [250 + 400*i, 100],
            'innerSize': '40%',
            'size': '75%',
            'name': cat[0],
            'data': map(lambda c: {
                'name': c,
                'y': value_or_zero(data, s, c, -1)/total*100
            }, cat)
        })
    
    options = {
        'chart': {'zoomType': 'xy'},
        'title': {'text': 'Energy usage distribution for heat production'},
        'subtitle': {'text': 'Scenario {0}'.format(s[-1])},
        'plotOptions': {
            'series': {
                'dataLabels': {
                    'enabled': True,
                    'color': '#000000',
                    'connectorColor': '#000000',
                    'formatter': 'testo'
                }
            }
        }
    }
    
    html.append(charts.plot(
        series,
        show='string',
        type='pie',
        stock=False,
        options=options,
        save='origin-of-heat-production-{0}.html'.format(s)
    ))
    
HTML(''.join(html))

###Distribution losses

In [25]:
losses = dict(zip(
    loaded_scenarios, 
    map(lambda x: np.array(monthly_diff(data[x], 'grid.Edis')) / np.array(monthly_diff(data[x], 'grid.Egrid'))*100, 
        loaded_scenarios)))

categories = [
    'januari', 
    'februari', 
    'maart', 
    'april', 
    'juni', 
    'juli',
    'augustus', 
    'september', 
    'oktober', 
    'november', 
    'december', 
    'year'
]
options = {
    'chart': {'zoomType': 'xy'},
    'title': {'text': 'Relative distribution losses throughout the year'},
    'xAxis': {
        'categories': categories
    },
    'yAxis': {
        'min': 0,
        'title': {'text': 'Distribution losses [%]'}
    }
}

series = map(lambda x: {
    'name': x,
    'data': losses[x]
}, loaded_scenarios)

charts.plot(
    type='column', 
    series=series, 
    options=options,
    stock=False,
    show='inline', 
    save=os.path.join(path, options['title']['text']) + '.html')

Possible explanations:
 - Losses are **not very dependent** of massflow. The higher the massflow, the more energy is distributed and the smaller the relative losses will be
 - S4 has the lowest energy needed due to the separate DHW production

In [52]:
x = np.linspace(0.01 ,0.1, 25)
y = 4180 * (70-((70-10)*np.exp(-1/(x*3600)))+10)

options = {
    'xAxis': {
        'title': {'text': 'Massflow [kg/s]'}
    },
    'yAxis': {
        'title': {'text': 'Heat losses [J]'}
    },
    'title': {'text': 'Volume heat losses'}
}

charts.plot(
    np.array([x,y]).T, 
    stock=False,
    options=options,
    show='inline'
)

###Load duration curves for the production site

In [26]:
def ldc(scenario, keys, sort='grid.Qgrid', rule='H', how='mean'):
    df = data[scenario]
    
    index = df.index
    sdf = df.sort(sort, ascending=False)[keys]
    sdf.index = index
    
    return sdf.resample(rule, how).dropna()

####Comparison of the scenarios

In [42]:
series = []

for s in loaded_scenarios:

    key = 'grid.Qhea'
    
    df = data[s].resample('H', 'max').dropna()
    index = df.index.asi8/1e6
    sdf = df[[key]].sort(key, ascending=False)

    values = sdf[key].values

    series.append({
        'name': s,
        'data': np.array([index, values]).T
    })

options = {
    'legend': {'enabled': True},
    'title': {'text': 'Load duration curve of the Grid heat consumption'},
    'yAxis': {'title': {'text': 'W'}},
    'height': 500,
    'chart': {
        'zoomType': 'xy'
    }
}
    
charts.plot(
    series, 
    options=options, 
    type='line', 
    save='load-duration-curve-grid.html',
    show='inline'
)

In [22]:
scs = ['S2', 'S3', 'S4']

key = 'grid.Qgrid'
minValue = 0e3

series = []

for s in set(loaded_scenarios).intersection(scs):
    df = data[s][[key]]
    load = df[df[key] > minValue]
    
    index = load.index.asi8/1e6
    values = load[key].values
    
    series.append({
        'name': s,
        'data': np.array([index, values]).T
    })
    
charts.plot(
    series, 
    options=options, 
    type='line', 
    show='tab'
)

Opening new tab...


####Breakdown of where the load is distributed to

In [28]:
keys = [
    'grid.Qsh', 
    'grid.Qdhw',
    'grid.Qdis',
    'productionSite.Qsto'
]

html = []

for s in loaded_scenarios:
    df = ldc(s, keys, rule='H', how='mean')

    options = {
        'legend': {'enabled': True},
        'plotOptions': {
            'area': {
                'stacking': 'normal'
            }
        },
        'title': {'text': 'LDC of the consumption'},
        'subtitle': {'text': 'Scenario {0}'.format(s[-1])},
        'height': 600
    }

    html.append(charts.plot(
        df,
        options=options, 
        type='area', 
        save='ldc-cons-' + s + '.html', 
        show='string'))
    
html = ''.join(html)

In [29]:
HTML(html)

####Breakdown of what is producing the load

In [25]:
keys = [
    'Qboi',
    'productionSite.Qhp',
    'productionSite.Qsun',
    'productionSite.QCHP'
]

html = []

for s in loaded_scenarios:
    df = ldc(s, keys, rule='H', how='mean')

    options = {
        'legend': {'enabled': True},
        'plotOptions': {
            'area': {
                'stacking': 'normal'
            }
        },
        'title': {'text': 'LDC of the production units'},
        'subtitle': {'text': 'Scenario {0}'.format(s[-1])},
        'height': 600
    }

    html.append(
        charts.plot(
            df, 
            options=options, 
            type='area', 
            save='ldc-prod-' + s + '.html', 
            show='string'))
    
HTML(''.join(html))

#### Load duration curve of the HP COPs


In [26]:
scs = ['S2', 'S3', 'S4']

key = 'productionSite.hp.COP'
series = []

for s in scs:
    cop = pd.DataFrame(ldc(s, [key], sort=key))
    
    index = cop.index.asi8/1e6
    values = cop[key].values
    
    series.append({
        'name': s,
        'data': np.array([index, values]).T
    })
    
options = {
    'legend': {'enabled': True},
    'title': {'text': 'COP values of the central Heat pumps'},
    'height': 600
}
    
charts.plot(
    series, 
    options=options, 
    type='line', 
    show='inline',
    save='COP.html', 
)

### Comfort evaluations

In [68]:
categories = [
    '.*TZoned'
]

options = {
    'chart': {'zoomType': 'xy'},
    'title': {'text': 'Average Thermal discomfort'},
    'xAxis': {
        'categories': categories
    },
    'yAxis': {
        'min': 0,
        'title': {'text': 'Kh'}
    }
}

def function(x):
    return {
        'name': x,
        'data': map(lambda c: data[x].filter(regex=c).sum(axis=1)[-1]/11, categories)
    }

series = map(lambda x: function(x), loaded_scenarios)

charts.plot(
    type='column', 
    series=series, 
    options=options,
    stock=False,
    show='inline', 
    save=os.path.join(path, options['title']['text']) + '.html')

In [14]:
houses = [
    u'grid.haarHakker1.',
    u'grid.haarHakker2.',
    u'grid.haarHakker3.',
    u'grid.haarHakker4.',
    u'grid.haarHakker5.',
    u'grid.peterslei1.',
    u'grid.peterslei2.',
    u'grid.peterslei3.',
    u'grid.peterslei4.',
    u'grid.peterslei5.',
    u'grid.peterslei6.'
]

In [46]:
for s in loaded_scenarios:
    df = data[s].filter(regex='.*TZone[^d]').resample('H', 'mean').dropna()
    options = {
        'legend': {'enabled': True},
        'title': {'text': 'Zone temperatures'},
        'subtitle': {'text': 'Scenario {0}'.format(s[-1])},
        'height': 600
    }

    html.append(
        charts.plot(
            df, 
            display=False,
            options=options, 
            type='line', 
            save=options['title']['text']+ '{0}.html'.format(s), 
            show='tab'))

Opening new tab...
Opening new tab...
Opening new tab...
Opening new tab...


In [38]:
TSet = 273.15+38
dhwd = dict()

import scipy.integrate as integrate

for s in loaded_scenarios:
    df = data[s]
    dhwd[s] = []
    for h in houses:
        ix = map(lambda i: not i, df[h + 'heatingSystem.mDhwReq'] > 0)
        df.loc[ix, h + '.heatingSystem.TDhwm'] = TSet
        df[h + 'heatingSystem.TDhwm'] = df[h + 'heatingSystem.TDhwm'] - TSet
        
        ts = df[h + 'heatingSystem.TDhwm']
        
        integ = integrate.trapz(ts, ts.index.astype(np.int64) / 10**9)
        
        dhwd[s].append(integ)

In [39]:
charts.plot(df.filter(regex='TDhwm').resample(how='max', rule='H'))

Opening new tab...


In [40]:
charts.plot(ts)
        
data[s][h + 'heatingSystem.TDhwm']
    
    


Opening new tab...


1970-01-08 00:03:20.000000   -1244.600006
1970-01-08 00:15:50.437500   -1244.600006
1970-01-08 00:18:50.437500   -1244.600006
1970-01-08 00:18:53.437500   -1244.600006
1970-01-08 00:18:55.500000   -1244.600006
1970-01-08 00:26:12.812500   -1244.600006
1970-01-08 00:36:40.000000   -1244.600006
1970-01-08 00:53:20.000000   -1244.600006
1970-01-08 01:26:40.000000   -1244.600006
1970-01-08 01:28:22.000000   -1244.600006
1970-01-08 01:37:47.375000   -1244.600006
1970-01-08 01:37:55.562500   -1244.600006
1970-01-08 01:37:59.500000   -1244.600006
1970-01-08 01:43:20.000000   -1244.600006
1970-01-08 02:06:47.062500   -1244.600006
1970-01-08 02:07:42.562500   -1244.600006
1970-01-08 02:14:10.062500   -1244.600006
1970-01-08 02:14:11.437500   -1244.600006
1970-01-08 02:15:41.062500   -1244.600006
1970-01-08 02:15:41.500000   -1244.600006
1970-01-08 02:16:40.000000   -1244.600006
1970-01-08 02:33:20.000000   -1244.600006
1970-01-08 02:37:25.625000   -1244.600006
1970-01-08 02:38:46.875000   -1244

In [67]:
charts.plot(df[['grid.haarHakker1.heatingSystem.mDhwReq', 'grid.haarHakker1.heatingSystem.TDhwm']])

Opening new tab...


In [18]:
type(df[h + 'heatingSystem.mDhw'])

pandas.core.series.Series

In [57]:
map(lambda x: not x, t)

[False, True]